In [76]:
import pandas as pd
import matplotlib.pyplot as plt
import py7zr
import numpy as np
import seaborn as sns
import psycopg2 as pg

In [77]:
#conexão com o banco de dados
conn = False
while not conn:
    try:
        conn = pg.connect(host="localhost",database="tp_sad", user="postgres", password="postgres")
    except:
        print("Erro: Falha ao conectar ao banco de dados!")
        print("Tentando novamente...")
        continue

In [78]:
def criaTabelas():
    sql = "create table dRaca( \
	IdRaca integer not null, \
	Descricao varchar(255), \
	constraint pkRaca primary key (IdRaca) \
); \
\
create table dDeficiencia( \
	IdDeficiencia integer not null,\
	Descricao varchar(255),\
	constraint pkDeficiencia primary key (IdDeficiencia)\
);\
\
create table dSexo(\
	IdSexo integer not null,\
	Descricao varchar(255),\
	constraint pkSexo primary key (IdSexo)\
);\
\
create table dTipoEmpregador(\
	IdTipoEmpregador integer not null,\
	Descricao varchar(255),\
	constraint pkTipoEmpregador primary key (IdTipoEmpregador)\
);\
\
create table dEscolaridade(\
	IdEscolaridade integer not null,\
	Descricao varchar(255),\
	constraint pkEscolaridade primary key (IdEscolaridade)\
);\
\
create table dMotivoMovimentacao(\
	IdMotivoMovimentacao integer not null,\
	Descricao varchar(255),\
	constraint pkMotivoMovimentacao primary key (IdMotivoMovimentacao)\
);\
\
create table dLocalizacao(\
	IdLocalizacao integer not null,\
	RegiaoGeografica varchar(255) not null,\
	UnidadeFederativa varchar(255) not null,\
	Municipio varchar(255) not null,\
	constraint pkLocalizacao primary key (IdLocalizacao)\
);\
\
create table dTempo(\
	IdTempo integer not null,\
	Ano integer not null,\
	Mes varchar(10) not null,\
	constraint pkTempo primary key (IdTempo)\
);\
\
create table dCargoDoEmpregado(\
	IdCBCO2002 integer not null,\
	Descricao varchar(255),\
	constraint pkCargoDoEmpregado primary key (IdCBCO2002)\
);\
\
create table dSetorDoEmpregador(\
	IdSetorDoEmpregador integer not null,\
	Descricao varchar(255),\
	constraint pkSetorDoEmpregador primary key (IdSetorDoEmpregador)\
);\
\
create table fMovimentacao(\
	IdTempo integer not null,\
	IdLocalizacao integer not null,\
	IdTipoEmpregador integer not null,\
	IdEscolaridade integer not null,\
	IdCargoDoEmpregado integer not null,\
	IdSetorDoEmpregador integer not null,\
	IdMotivoMovimentacao integer not null,\
	IdRaca integer not null,\
	IdSexo integer not null,\
	IdDeficiencia integer not null,\
	Idade integer not null,\
	Salario real not null,\
	HorasContratuaisSemanais integer not null,\
	TipoMovimentacao integer not null, \
	\
	constraint fkMovimentacaoTempo foreign key (IdTempo) references dTempo(IdTempo),\
	constraint fkMovimentacaoLocalizacao foreign key (IdLocalizacao) references dLocalizacao(IdLocalizacao),\
	constraint fkMovimentacaoTipoEmpregador foreign key (IdTipoEmpregador) references dTipoEmpregador(IdTipoEmpregador),\
	constraint fkMovimentacaoEscolaridade foreign key (IdEscolaridade) references dEscolaridade(IdEscolaridade),\
	constraint fkMovimentacaoCargoDoEmpregado foreign key (IdCargoDoEmpregado) references dCargoDoEmpregado(IdCBCO2002),\
	constraint fkMovimentacaoSetorDoEmpregador foreign key (IdSetorDoEmpregador) references dSetorDoEmpregador(IdSetorDoEmpregador),\
	constraint fkMovimentacaoRaca foreign key (IdRaca) references dRaca(IdRaca),\
	constraint fkMovimentacaoSexo foreign key (IdSexo) references dSexo(IdSexo),\
	constraint fkMovimentacaoDeficiencia foreign key (IdDeficiencia) references dDeficiencia(IdDeficiencia)\
);"

    cur = conn.cursor()
    cur.execute(sql)
    conn.commit()
    cur.close()
    

In [79]:
#competênciamov;região;uf;município;seção;subclasse;saldomovimentação;cbo2002ocupação;categoria;graudeinstrução;idade;horascontratuais;raçacor;sexo;tipoempregador;tipoestabelecimento;tipomovimentação;tipodedeficiência;indtrabintermitente;indtrabparcial;salário;tamestabjan;indicadoraprendiz;origemdainformação;competênciadec;indicadordeforadoprazo;unidadesaláriocódigo;valorsaláriofixo
ListaDeColunasDoNovoCAGED = ['competênciamov', 'região', 'uf', 'município', 'seção', 'subclasse', 'saldomovimentação', 'cbo2002ocupação', 'categoria', 'graudeinstrução', 'idade', 'horascontratuais', 'raçacor', 'sexo', 'tipoempregador', 'tipoestabelecimento', 'tipomovimentação', 'tipodedeficiência', 'indtrabintermitente', 'indtrabparcial', 'salário', 'tamestabjan', 'indicadoraprendiz', 'origemdainformação', 'competênciadec', 'indicadordeforadoprazo', 'unidadesaláriocódigo', 'valorsaláriofixo']
ListaDeColunasDoNovoCAGED_filtrado = ['região', 'uf', 'município', 'saldomovimentação', 'cbo2002ocupação', 'subclasse', 'graudeinstrução', 'idade', 'horascontratuais', 'raçacor', 'sexo', 'tipoestabelecimento', 'tipomovimentação', 'tipodedeficiência', 'salário']

#ListaDeColunasDoNovoCAGED_filtrado = ['regiãof', 'uff', 'municípiof', 'saldomovimentaçãof', 'cbo2002ocupaçãof', 'subclassef', 'graudeinstruçãof', 'idadef', 'horascontratuaisf', 'raçacorf', 'sexof', 'tipoempregador', 'tipomovimentação', 'tipodedeficiênciaf', 'saláriof']
#Admitidos/Desligados;Competência Declarada;Município;Ano Declarado;CBO 2002 Ocupação;CNAE 1.0 Classe;CNAE 2.0 Classe;CNAE 2.0 Subclas;Faixa Empr Início Jan;Grau Instrução;Qtd Hora Contrat;IBGE Subsetor;Idade;Ind Aprendiz;Ind Portador Defic;Raça Cor;Salário Mensal;Saldo Mov;Sexo;Tempo Emprego;Tipo Estab;Tipo Defic;Tipo Mov Desagregado;UF;Bairros SP;Bairros Fortaleza;Bairros RJ;Distritos SP;Regiões Adm DF;Mesorregião;Microrregião;Região Adm RJ;Região Adm SP;Região Corede;Região Corede 04;Região Gov SP;Região Senac PR;Região Senai PR;Região Senai SP;Sub-Região Senai PR;Ind Trab Parcial;Ind Trab Intermitente
ListaDeColunasDoAntigoCAGED = ['Admitidos/Desligados', 'Competência Declarada', 'Município', 'Ano Declarado', 'CBO 2002 Ocupação', 'CNAE 1.0 Classe', 'CNAE 2.0 Classe', 'CNAE 2.0 Subclas', 'Faixa Empr Início Jan', 'Grau Instrução', 'Qtd Hora Contrat', 'IBGE Subsetor', 'Idade', 'Ind Aprendiz', 'Ind Portador Defic', 'Raça Cor', 'Salário Mensal', 'Saldo Mov', 'Sexo', 'Tempo Emprego', 'Tipo Estab', 'Tipo Defic', 'Tipo Mov Desagregado', 'UF', 'Bairros SP', 'Bairros Fortaleza', 'Bairros RJ', 'Distritos SP', 'Regiões Adm DF', 'Mesorregião', 'Microrregião', 'Região Adm RJ', 'Região Adm SP', 'Região Corede', 'Região Corede 04', 'Região Gov SP', 'Região Senac PR', 'Região Senai PR', 'Região Senai SP', 'Sub-Região Senai PR', 'Ind Trab Parcial', 'Ind Trab Intermitente']
ListaDeColunasDoAntigoCAGED_filtrado = ['UF', 'Município', 'Saldo Mov', 'CBO 2002 Ocupação', 'CNAE 2.0 Subclas', 'Grau Instrução', 'Idade', 'Qtd Hora Contrat', 'Raça Cor', 'Sexo', 'Tipo Estab', 'Tipo Mov Desagregado', 'Tipo Defic', 'Salário Mensal']

In [80]:
def addLocalizacao(Localizacao):
    sql = f"INSERT INTO dLocalizacao (IdLocalizacao, RegiaoGeografica, UnidadeFederativa, Municipio) VALUES ({Localizacao[0]}, '{Localizacao[1]}', '{Localizacao[2]}', '{Localizacao[3]}')"
    cur = conn.cursor()
    cur.execute(sql)
    conn.commit()
    cur.close()

def criaObjectLocalizacao(regioes, ufs, municipios):
    for municipio in municipios:
        id_municipio = municipio
        regiao = regioes[int(str(municipio)[:1])]
        uf = ufs[int(str(municipio)[:2])]
        nome_municipio = municipios[municipio]
        Localizacao = [id_municipio, regiao, uf, nome_municipio]
        addLocalizacao(Localizacao)

def addCBO(CBO):
    sql = f"INSERT INTO dCargoDoEmpregado (IdCBCO2002, Descricao) VALUES ({CBO[0]}, '{CBO[1]}')"
    cur = conn.cursor()
    cur.execute(sql)
    conn.commit()
    cur.close()

def addGrauInstrucao(GrauInstrucao):
    sql = f"INSERT INTO dEscolaridade (IdEscolaridade, Descricao) VALUES ({GrauInstrucao[0]}, '{GrauInstrucao[1]}')"
    cur = conn.cursor()
    cur.execute(sql)
    conn.commit()
    cur.close()

def addRacaCor(RacaCor):
    sql = f"INSERT INTO dRaca (IdRaca, Descricao) VALUES ({RacaCor[0]}, '{RacaCor[1]}')"
    cur = conn.cursor()
    cur.execute(sql)
    conn.commit()
    cur.close()

def addSexo(Sexo):
    sql = f"INSERT INTO dSexo (IdSexo, Descricao) VALUES ({Sexo[0]}, '{Sexo[1]}')"
    cur = conn.cursor()
    cur.execute(sql)
    conn.commit()
    cur.close()

def addTipoDeficiencia(TipoDeficiencia):
    sql = f"INSERT INTO dDeficiencia (IdDeficiencia, Descricao) VALUES ({TipoDeficiencia[0]}, '{TipoDeficiencia[1]}')"
    cur = conn.cursor()
    cur.execute(sql)
    conn.commit()
    cur.close()

def addTipoEmpregador(TipoEntrgador):
    sql = f"INSERT INTO dTipoEmpregador (IdTipoEmpregador, Descricao) VALUES ({TipoEntrgador[0]}, '{TipoEntrgador[1]}')"
    cur = conn.cursor()
    cur.execute(sql)
    conn.commit()
    cur.close()
    

def addMotivoMovimentacao(MotivoMovimentacao):
    sql = f"INSERT INTO dMotivoMovimentacao (IdMotivoMovimentacao, Descricao) VALUES ({MotivoMovimentacao[0]}, '{MotivoMovimentacao[1]}')"
    cur = conn.cursor()
    cur.execute(sql)
    conn.commit()
    cur.close()

def addTempo(Tempo):
    sql = f"INSERT INTO dTempo (IdTempo, Ano, Mes) VALUES ({Tempo[0]}, {Tempo[1]}, {Tempo[2]})"
    cur = conn.cursor()
    cur.execute(sql)
    conn.commit()
    cur.close()

def selectIdLocalizacao(Localizacao):
    print(Localizacao)
    print(f'SELECT IdLocalizacao FROM dLocalizacao WHERE IdLocalizacao = {Localizacao}')
    sql = f"SELECT IdLocalizacao FROM dLocalizacao WHERE IdLocalizacao = {Localizacao}"
    cur = conn.cursor()
    cur.execute(sql)
    idLocalizacao = cur.fetchone()
    cur.close()
    return idLocalizacao[0]

def selectTipoEmpregador(TipoEmpregador):
    sql = f"SELECT IdTipoEmpregador FROM dTipoEmpregador WHERE IdTipoEmpregador = {TipoEmpregador}"
    cur = conn.cursor()
    cur.execute(sql)
    idLocalizacao = cur.fetchone()
    cur.close()
    return idLocalizacao[0]


def addSubClasse(SubClasse):
    sql = f"INSERT INTO dSetorDoEmpregador (IdSetorDoEmpregador, Descricao) VALUES ({SubClasse[0]}, '{SubClasse[1]}')"
    cur = conn.cursor()
    cur.execute(sql)
    conn.commit()
    cur.close()



In [81]:
criaTabelas()
Regioes = {}
UFs = {}
Municipios = {}
for i in ListaDeColunasDoNovoCAGED:
    try:
        legenda_dados = pd.read_excel('LayoutNovoCaged.xlsx', sheet_name=f'{i}')
        if i == 'região':
            for i in range(len(legenda_dados['Código'])):
                Regioes[legenda_dados['Código'][i]] = legenda_dados['Descrição'][i]
        elif i == 'uf':
            for i in range(len(legenda_dados['Código'])):
                UFs[legenda_dados['Código'][i]] = legenda_dados['Descrição'][i]
        elif i == 'município':
            for i in range(len(legenda_dados['Código'])):
                Municipios[legenda_dados['Código'][i]] = legenda_dados['Descrição'][i]
        elif i == 'cbo2002ocupação':
            for i in range(len(legenda_dados['Código'])):
                CBO = [legenda_dados['Código'][i], legenda_dados['Descrição'][i]]
                addCBO(CBO)
        elif i == 'subclasse':
            for i in range(len(legenda_dados['Código'])):
                SubClasse = [legenda_dados['Código'][i], legenda_dados['Descrição'][i]]
                addSubClasse(SubClasse)
        elif i == 'graudeinstrução':
            for i in range(len(legenda_dados['Código'])):
                GrauInstrucao = [legenda_dados['Código'][i], legenda_dados['Descrição'][i]]
                addGrauInstrucao(GrauInstrucao)
        elif i == 'raçacor':
            for i in range(len(legenda_dados['Código'])):
                RacaCor = [legenda_dados['Código'][i], legenda_dados['Descrição'][i]]
                addRacaCor(RacaCor)
        elif i == 'sexo':
            for i in range(len(legenda_dados['Código'])):
                Sexo = [legenda_dados['Código'][i], legenda_dados['Descrição'][i]]
                addSexo(Sexo)
        elif i == 'tipoestabelecimento':
            for i in range(len(legenda_dados['Código'])):
                TipoEmpregador = [legenda_dados['Código'][i], legenda_dados['Descrição'][i]]
                addTipoEmpregador(TipoEmpregador)
        elif i == 'tipodedeficiência':
            for i in range(len(legenda_dados['Código'])):
                TipoDeficiencia = [legenda_dados['Código'][i], legenda_dados['Descrição'][i]]
                addTipoDeficiencia(TipoDeficiencia)
        elif i == 'tipomovimentação':
            for i in range(len(legenda_dados['Código'])):
                MotivoMovimentacao = [legenda_dados['Código'][i], legenda_dados['Descrição'][i]]
                addMotivoMovimentacao(MotivoMovimentacao)        
    except Exception as e:
        print(f"Erro: {e}")
        continue

criaObjectLocalizacao(Regioes, UFs, Municipios)

Erro: Worksheet named 'competênciamov' not found
Erro: Worksheet named 'saldomovimentação' not found
Erro: Worksheet named 'idade' not found
Erro: Worksheet named 'horascontratuais' not found
Erro: Worksheet named 'salário' not found
Erro: Worksheet named 'competênciadec' not found
Erro: Worksheet named 'valorsaláriofixo' not found


In [82]:
#Criando um csv com os dados do tempo
df_tempo = pd.DataFrame(columns=['Id', 'Ano', 'Mês'])

Meses = ['Janeiro', 'Fevereiro', 'Março', 'Abril', 'Maio', 'Junho', 'Julho',
            'Agosto', 'Setembro', 'Outubro', 'Novembro', 'Dezembro']
i = 1
ano = 2018
mes = 1
while(ano<=2023):
    while(mes<13):
        df_tempo.loc[i] = [i, ano, Meses[mes-1]]
        addTempo([i, ano, mes])
        i = i+1
        mes = mes+1
    ano = ano+1
    mes = 1

df_tempo.to_csv(f'./tempo.csv', index=False)

In [83]:
def addFMovimentacao(Movimentacao):
    sql = f"INSERT INTO fMovimentacao (IdTempo, IdLocalizacao, IdTipoEmpregador, IdEscolaridade, IdCargoDoEmpregado, IdSetorDoEmpregador, IdMotivoMovimentacao, IdRaca, IdSexo, IdDeficiencia, Idade, Salario, HorasContratuaisSemanais, TipoMovimentacao) VALUES ({Movimentacao[0]}, {Movimentacao[1]}, {Movimentacao[2]}, {Movimentacao[3]}, {Movimentacao[4]}, {Movimentacao[5]}, {Movimentacao[6]}, {Movimentacao[7]}, {Movimentacao[8]}, {Movimentacao[9]}, {Movimentacao[10]}, {Movimentacao[11]}, {Movimentacao[12]}, {Movimentacao[13]})"
    cur = conn.cursor()
    cur.execute(sql)
    conn.commit()
    cur.close()

In [84]:
ano = 2018
mes = 1
Path = None
df = None
NovoCAGED = True
while(ano<=2023):
    if(ano<=2019):
        ListaDeColunasDoAntigoCAGED_filtrado.append('Competência Declarada')
        while(mes<=12):
            print(f'Ano: {ano} Mês: {mes}')
            if(mes<10):
                Path = (f'./ANTIGO_CAGED/{ano}/CAGEDEST_0{mes}{ano}.7z')
            else:
                Path = (f'./ANTIGO_CAGED/{ano}/CAGEDEST_{mes}{ano}.7z')
            print(f'Path do arquivo zip: {Path}')
            try:
                NovoCAGED = False
                with py7zr.SevenZipFile(Path, mode='r') as z:
                    z.extractall(path=f'./ANTIGO_CAGED/{ano}')
                Path = Path.replace('.7z', '.txt')
                df_prov = pd.read_csv(Path, sep=';', encoding='latin-1', usecols=ListaDeColunasDoAntigoCAGED_filtrado)
                if(df is None):
                    df = df_prov
                else:
                    df = pd.concat([df, df_prov])
                mes = mes+1
            except Exception as e:
                print(f'Error ao ler o arquivo: {Path}')
                print(f'Erro: {e}')
                mes = mes+1
                continue
        #Processo de ETL
        if(mes==13):
            df['Competência Declarada'] = df['Competência Declarada'].astype(str)
            df['Mês'] = df['Competência Declarada'].str[4:6].astype(int)
            df['Ano'] = df['Competência Declarada'].str[0:4].astype(int)
            df['UF'] = df['UF'].astype(str)
            #usar operador ternário para criar a coluna Região
            df['Região'] = df['UF'].str[0:1].astype(int) 
            i_tempo = 1
            ano_tempo = 2018
            mes_tempo = 1
            while(ano_tempo<=2023):
                while(mes_tempo<13):
                    df.loc[(df['Ano'] == ano_tempo) & (df['Mês'] == mes_tempo), 'Id Tempo'] = int(i_tempo)
                    i_tempo = i_tempo+1
                    mes_tempo = mes_tempo+1
                ano_tempo = ano_tempo+1
                mes_tempo = 1
            df['Grau Instrução'] = df['Grau Instrução'].replace(-1, 9).astype(int)
            df['Sexo'] = df['Sexo'].replace(-1, 9).astype(int)
            df['Sexo'] = df['Sexo'].replace(2, 3).astype(int)
            df['Tipo Defic'] = df['Tipo Defic'].replace(-1, 9).astype(int)
            df['Tipo Estab'] = df['Tipo Estab'].replace(3, 5).astype(int)
            df['Tipo Estab'] = df['Tipo Estab'].replace(-1, 9).astype(int)
            df['Tipo Mov Desagregado'] = df['Tipo Mov Desagregado'].replace(-1, 99).astype(int)
            df['Tipo Mov Desagregado'] = df['Tipo Mov Desagregado'].replace(1, 10).astype(int)
            df['Tipo Mov Desagregado'] = df['Tipo Mov Desagregado'].replace(2, 20).astype(int)
            df['Tipo Mov Desagregado'] = df['Tipo Mov Desagregado'].replace(3, 70).astype(int)
            df['Tipo Mov Desagregado'] = df['Tipo Mov Desagregado'].replace(4, 31).astype(int)
            df['Tipo Mov Desagregado'] = df['Tipo Mov Desagregado'].replace(5, 32).astype(int)
            df['Tipo Mov Desagregado'] = df['Tipo Mov Desagregado'].replace(6, 40).astype(int)
            df['Tipo Mov Desagregado'] = df['Tipo Mov Desagregado'].replace(7, 50).astype(int)
            df['Tipo Mov Desagregado'] = df['Tipo Mov Desagregado'].replace(8, 60).astype(int)
            df['Tipo Mov Desagregado'] = df['Tipo Mov Desagregado'].replace(9, 80).astype(int)
            df['Tipo Mov Desagregado'] = df['Tipo Mov Desagregado'].replace(10, 35).astype(int)
            df['Tipo Mov Desagregado'] = df['Tipo Mov Desagregado'].replace(11, 36).astype(int)
            df['Raça Cor'] = df['Raça Cor'].astype(int)
            df['Raça Cor'] = df['Raça Cor'] * 10
            df['Raça Cor'] = df['Raça Cor'].replace(-10, 6).astype(int)
            df['Raça Cor'] = df['Raça Cor'].replace(10, 5).astype(int)
            df['Raça Cor'] = df['Raça Cor'].replace(20, 1).astype(int)
            df['Raça Cor'] = df['Raça Cor'].replace(40, 2).astype(int)
            df['Raça Cor'] = df['Raça Cor'].replace(60, 4).astype(int)
            df['Raça Cor'] = df['Raça Cor'].replace(80, 3).astype(int)
            df['Raça Cor'] = df['Raça Cor'].replace(90, 9).astype(int)
            df['Id Tempo'] = df['Id Tempo'].astype(int)
            #Remover coluna 'Competência Declarada'
            ListaDeColunasDoAntigoCAGED_filtrado.remove('Competência Declarada')
            FMovimentacao = []
            print(f'Salvando no banco o ano: {ano}')
            for index, row in df.iterrows():
                Movimentacao = [row['Id Tempo'], row['Município'], row['Tipo Estab'], row['Grau Instrução'], row['CBO 2002 Ocupação'], row['CNAE 2.0 Subclas'], row['Tipo Mov Desagregado'], row['Raça Cor'], row['Sexo'], row['Tipo Defic'], row['Idade'], str(row['Salário Mensal']).replace(',', '.'), row['Qtd Hora Contrat'], row['Saldo Mov']]
                addFMovimentacao(Movimentacao)
    else:
        ListaDeColunasDoNovoCAGED_filtrado.append('competênciamov')
        while(mes<=12):
            print(f'Ano: {ano} Mês: {mes}')
            if(mes<10):
                Path = (f'./NOVO_CAGED/{ano}/{ano}0{mes}/CAGEDMOV{ano}0{mes}.7z')
            else:
                Path = (f'./NOVO_CAGED/{ano}/{ano}{mes}/CAGEDMOV{ano}{mes}.7z')
            print(f'Path do arquivo zip: {Path}')
            try:
                NovoCAGED = True
                with py7zr.SevenZipFile(Path, mode='r') as z:
                    if (mes<10):
                        z.extractall(path=f'./NOVO_CAGED/{ano}/{ano}0{mes}')
                    else:
                        z.extractall(path=f'./NOVO_CAGED/{ano}/{ano}{mes}')
                Path = Path.replace('.7z', '.txt')
                df_prov = pd.read_csv(Path, sep=';', usecols=ListaDeColunasDoNovoCAGED_filtrado)
                if(df is None):
                    df = df_prov
                else:
                    df = pd.concat([df, df_prov])
                mes = mes+1
            except Exception as e:
                print(f'Error ao ler o arquivo: {Path}')
                print(f'Erro: {e}')
                mes = mes+1
                continue
        #Processo de ETL
        if(mes==13):
            #df['competênciamov'] formato AAAAMM
            df['competênciamov'] = df['competênciamov'].astype(str)
            df['Mês'] = df['competênciamov'].str[4:6].astype(int)
            df['Ano'] = df['competênciamov'].str[0:4].astype(int)
            i_tempo = 1
            ano_tempo = 2018
            mes_tempo = 1
            while(ano_tempo<=2023):
                while(mes_tempo<13):
                    df.loc[(df['Ano'] == ano_tempo) & (df['Mês'] == mes_tempo), 'Id Tempo'] = int(i_tempo)
                    i_tempo = i_tempo+1
                    mes_tempo = mes_tempo+1
                ano_tempo = ano_tempo+1
                mes_tempo = 1
            df['Id Tempo'] = df['Id Tempo'].astype(int)
            #Remover coluna 'competênciamov'
            ListaDeColunasDoNovoCAGED_filtrado.remove('competênciamov')
            FMovimentacao = []
            print(f'Salvando no banco o ano: {ano}')
            for index, row in df.iterrows():
                Movimentacao = [row['Id Tempo'], row['município'], row['tipoestabelecimento'], row['graudeinstrução'], row['cbo2002ocupação'], row['subclasse'], row['tipomovimentação'], row['raçacor'], row['sexo'], row['tipodedeficiência'], row['idade'], str(row['salário']).replace(',', '.'), row['horascontratuais'], row['saldomovimentação']]
                addFMovimentacao(Movimentacao)
            mes = mes+1
    #Amostragem de 5% do df
    if(NovoCAGED):
        ListaDeColunasDoNovoCAGED_filtrado.append('Id Tempo')
        df = df[ListaDeColunasDoNovoCAGED_filtrado]
        ListaDeColunasDoNovoCAGED_filtrado.remove('Id Tempo')
    else:
        ListaDeColunasDoAntigoCAGED_filtrado.append('Região')
        ListaDeColunasDoAntigoCAGED_filtrado.append('Id Tempo')
        df = df[ListaDeColunasDoAntigoCAGED_filtrado]
        ListaDeColunasDoAntigoCAGED_filtrado.remove('Região')
        ListaDeColunasDoAntigoCAGED_filtrado.remove('Id Tempo')
    df_amostra = df.sample(frac=.05)
    df_amostra.to_csv(f'./CAGEDMOV{ano}_amostra.csv', index=False, encoding='utf-8')
    #Salvar o df em arquivo .csv
    df.to_csv(f'./CAGEDMOV{ano}.csv', index=False, encoding='utf-8')
    #Limpar o df
    df = None
    ano = ano+1
    mes = 1


Ano: 2018 Mês: 1
Path do arquivo zip: ./ANTIGO_CAGED/2018/CAGEDEST_012018.7z
Ano: 2018 Mês: 2
Path do arquivo zip: ./ANTIGO_CAGED/2018/CAGEDEST_022018.7z
Ano: 2018 Mês: 3
Path do arquivo zip: ./ANTIGO_CAGED/2018/CAGEDEST_032018.7z
Ano: 2018 Mês: 4
Path do arquivo zip: ./ANTIGO_CAGED/2018/CAGEDEST_042018.7z
Ano: 2018 Mês: 5
Path do arquivo zip: ./ANTIGO_CAGED/2018/CAGEDEST_052018.7z
Ano: 2018 Mês: 6
Path do arquivo zip: ./ANTIGO_CAGED/2018/CAGEDEST_062018.7z
Ano: 2018 Mês: 7
Path do arquivo zip: ./ANTIGO_CAGED/2018/CAGEDEST_072018.7z
Ano: 2018 Mês: 8
Path do arquivo zip: ./ANTIGO_CAGED/2018/CAGEDEST_082018.7z
Ano: 2018 Mês: 9
Path do arquivo zip: ./ANTIGO_CAGED/2018/CAGEDEST_092018.7z
Ano: 2018 Mês: 10
Path do arquivo zip: ./ANTIGO_CAGED/2018/CAGEDEST_102018.7z
Ano: 2018 Mês: 11
Path do arquivo zip: ./ANTIGO_CAGED/2018/CAGEDEST_112018.7z
Ano: 2018 Mês: 12
Path do arquivo zip: ./ANTIGO_CAGED/2018/CAGEDEST_122018.7z
1
[1, 110004, 1, 8, 322415, 8630504, 40, 1, 3, 0, 23, '000520.00', 44, -1